In [32]:
import pandas as pd
import glob
import requests
from playwright.sync_api import sync_playwright
import time
from bs4 import BeautifulSoup
import random


In [35]:
import asyncio
from playwright.async_api import async_playwright

url = "https://www.arbeitsagentur.de/jobsuche/suche?angebotsart=1&was=KI"
async def main():
    async with async_playwright() as p:
        browser = await p.chromium.launch(headless=False)
        page = await browser.new_page()
        await page.goto(url)
        html = await page.content()
        for i in range(1, 75): 
            sleep_time = random.uniform(5, 10)
            await page.wait_for_selector("#ergebnisliste-ladeweitere-button")
            await page.click("#ergebnisliste-ladeweitere-button")   
            time.sleep(sleep_time)
        safe_html = await page.content()
        print(html)
        elements = await page.query_selector_all('.oben.ng-star-inserted')

        texts = [await el.inner_text() for el in elements]
        print(texts)
        return(safe_html)
        #await browser.close()

html_safe=await main()
html_safe

<!DOCTYPE html><html lang="de" data-beasties-container="" class="hydrated"><head>
  <title>KI - Jobsuche der BA</title>

  <meta name="google-site-verification" content="p13Ggb4Cq78RdCjrz7uf5wUo_74UB3TigT6o9yk5xz8">

  <base href="/jobsuche/">

  <meta charset="utf-8"><style data-styles="">ba-feedback{visibility:hidden}.hydrated{visibility:inherit}</style><style data-styles="">oiam-oauth-component{visibility:hidden}.hydrated{visibility:inherit}</style><style data-styles="">slot-fb{display:contents}slot-fb[hidden]{display:none}auth-level-with-status,authn-level-shield,bahf-cd-checkbox,bahf-cd-collapse,bahf-cd-modal,bahf-cookie-disclaimer-dpl3,bahf-footer,bahf-header,bahf-header-lang-switch-list-item,bahf-header-megaflyout,bahf-i18n,bahf-language-switch-desktop,bahf-language-switch-mobile,bahf-maintenance-info,event-buttons,mock-header,profile-header-event-buttons,profile-menu,profile-menu-bahf-i18n,session-expiration-30m-warn-popup,session-expiration-5m-warn-popup,session-expiration-ina

'<!DOCTYPE html><html lang="de" data-beasties-container="" class="hydrated"><head>\n  <title>KI - Jobsuche der BA</title>\n\n  <meta name="google-site-verification" content="p13Ggb4Cq78RdCjrz7uf5wUo_74UB3TigT6o9yk5xz8">\n\n  <base href="/jobsuche/">\n\n  <meta charset="utf-8"><style data-styles="">ba-feedback{visibility:hidden}.hydrated{visibility:inherit}</style><style data-styles="">oiam-oauth-component{visibility:hidden}.hydrated{visibility:inherit}</style><style data-styles="">slot-fb{display:contents}slot-fb[hidden]{display:none}auth-level-with-status,authn-level-shield,bahf-cd-checkbox,bahf-cd-collapse,bahf-cd-modal,bahf-cookie-disclaimer-dpl3,bahf-footer,bahf-header,bahf-header-lang-switch-list-item,bahf-header-megaflyout,bahf-i18n,bahf-language-switch-desktop,bahf-language-switch-mobile,bahf-maintenance-info,event-buttons,mock-header,profile-header-event-buttons,profile-menu,profile-menu-bahf-i18n,session-expiration-30m-warn-popup,session-expiration-5m-warn-popup,session-expira

In [38]:
# Suppose html_safe contains your HTML as a string
soup = BeautifulSoup(html_safe, "html.parser")

# Find all elements with the class "oben ng-star-inserted"
elements = soup.find_all(class_="mitte-links-titel")

# Get their inner text
texts = [el.get_text(strip=True) for el in elements]
texts


['Product Owner KI (m/w/d)',
 'KI-Systementwickler (w/m/d)',
 'KI-Ingenieur*in (m/w/d)',
 'KI-Solution Manager (m/w/d)',
 'KI-Entwickler (m/w/d)',
 'Projektmanager für KI Projekte (m/w/d)',
 'KI Projektmanager\xa0(m/w/d)',
 'KI- und Digitalisierungsmanager m/w/d',
 'Referentin/Referent (m/w/d) KI-basierte Gesteinsanalytik',
 'KI-Lab Manager (w/m/d)',
 'KI-Developer',
 'Projektmitarbeiterin (w/m/d) KI-Recht',
 'Senior IT-Sicherheitskoordinator KI (m/w/d)',
 'Produktmanager:in KI-Seminarportfolio B2B',
 'KI Produktmanager\xa0(m/w/d)',
 'KI Entwickler (m/w/d)',
 'Kreativer Kopf mit KI-Leidenschaft (m/w/d)',
 'KI-Architekt*in (w/m/d)',
 'NLP / KI Experte (m/w/d)',
 'KI Software Automation Engineer (m/w/d)',
 'Prozessmanager KI (m/w/d)',
 'KI Manager & Dozent (m/w/d)',
 'Aktuar/in Risiko Manager - KI (m/w/d)',
 'KI Senior Entwickler (m/w/d)',
 'Aktuar/in Risiko Manager - KI (m/w/d)',
 'Projektbegleitung (m/w/d) - KI-Entwicklung',
 'KI / Data Engineer (m/w/d)',
 'Senior Software-Entwickler*i

In [39]:
len(texts)

1867

In [40]:
divs = soup.find_all("div", class_="oben")
spans = []
for div in divs:
    spans.extend(div.find_all("span"))

# If you want their text:
span_texts = [span.get_text(strip=True) for span in spans]
len(span_texts)

1867

In [44]:
filtered_unique=set(span_texts)
len(filtered_unique)

521

In [48]:
jobs=pd.DataFrame([span_texts]).T

In [49]:
jobs.columns=["job_title"]
jobs

job_title
0                                   Product Owner
1                   Ingenieur/in - Elektrotechnik
2                           Systeminformatiker/in
3                                   KI-Manager/in
4                           Softwareentwickler/in
...                                           ...
1862                         Betriebsingenieur/in
1863              Ingenieur/in - Werkstofftechnik
1864  Ausbilder/in - Anerkannte Ausbildungsberufe
1865                              Modedesigner/in
1866                         IT-Kundenbetreuer/in

[1867 rows x 1 columns]

In [51]:
jobtitle=jobs.groupby("job_title").size().reset_index(name='counts').sort_values(by='counts', ascending=False)
jobtitle

job_title  counts
246                           Informatiker/in      92
447                     Softwareentwickler/in      66
258             Ingenieur/in - Elektrotechnik      48
515        Wissenschaftliche/r Mitarbeiter/in      46
264               Ingenieur/in - Maschinenbau      43
..                                        ...     ...
237          Idea- und Innovations-Manager/in       1
234                        IT-Systemplaner/in       1
232                  IT-System-Kaufmann/-frau       1
230              IT-Sicherheitskoordinator/in       1
520  Zweiradmechatroniker/in - Fahrradtechnik       1

[521 rows x 2 columns]

In [56]:
jobtitle[jobtitle["counts"]>5]

job_title  counts
246                     Informatiker/in      92
447               Softwareentwickler/in      66
258       Ingenieur/in - Elektrotechnik      48
515  Wissenschaftliche/r Mitarbeiter/in      46
264         Ingenieur/in - Maschinenbau      43
..                                  ...     ...
117                        Einkäufer/in       6
334              Managementassistent/in       6
302              Key-Account-Manager/in       6
308    Konstrukteur/in - Elektrotechnik       6
357    Medizinische/r Fachangestellte/r       6

[72 rows x 2 columns]

In [55]:
jobtitle[jobtitle["counts"]>5].to_csv("jobtitle.csv", index=False)

In [6]:
data_not_na=data[~data["einheit_mastr_nummer"].isna()]
data_not_na

goal100_id einheit_mastr_nummer               behoerden_einheit_id  \
0           36019      SEE966958743041                                NaN   
4           79220      SEE970653437198                SH-03000924205-0002   
5           77800      SEE930060808431                SH-03000924233-0001   
6           78441      SEE948056013141                SH-51001900011-0004   
7           79178      SEE969313089747                SH-51001900011-0001   
...           ...                  ...                                ...   
42663       41655      SEE905015577458                                NaN   
42664       41828      SEE929841659676                                NaN   
42665       29924      SEE924115847834                                NaN   
42666       24143      SEE924538245743                SN-09000000004-0002   
42667       24769      SEE998013206017  TH-FAWIND-GOAL100-SEE998013206017   

                      name_windpark     name_stromerzeugungseinheit  \
0                               NaN  HS-Flensburg_P00012_W+PV_202kW   
4              Windpark Lübeck Nord                 WEA2 Pöppendorf   
5                    Bültwind Nr.60                        Bültwind   
6         Bürgerwindpark Albersdorf                WEA 4 / V 203772   
7         Bürgerwindpark Albersdorf                WEA 1 / V 203769   
...                             ...                             ...   
42663  meridian Windpark Thonhausen                           WEA 4   
42664  meridian Windpark Thonhausen                           WEA 7   
42665  meridian Windpark Thonhausen                           WEA 6   
42666      Mark Sahnau / Thonhausen                Mark Sahnau WEA2   
42667      Mark Sahnau / Thonhausen                 Thonhausen WEA6   

      einheit_betriebsstatus  ags_gemeinde          bundesland  \
0                 In Betrieb     1001000.0  Schleswig-Holstein   
4                 In Betrieb     1003000.0  Schleswig-Holstein   
5                 In Betrieb     1003000.0  Schleswig-Holstein   
6                 In Betrieb     1051001.0  Schleswig-Holstein   
7                 In Betrieb     1051001.0  Schleswig-Holstein   
...                      ...           ...                 ...   
42663             In Betrieb    16077047.0           Thüringen   
42664             In Betrieb    16077047.0           Thüringen   
42665             In Betrieb    16077047.0           Thüringen   
42666             In Betrieb    16077047.0           Thüringen   
42667             In Betrieb    16077047.0           Thüringen   

              landkreis    gemeinde  ... dauer_genehmigung dauer_realisierung  \
0             Flensburg   Flensburg  ...               NaN                NaN   
4                Lübeck      Lübeck  ...             203.0              539.0   
5                Lübeck      Lübeck  ...               NaN                NaN   
6          Dithmarschen  Albersdorf  ...             258.0              192.0   
7          Dithmarschen  Albersdorf  ...             258.0              193.0   
...                 ...         ...  ...               ...                ...   
42663  Altenburger Land  Thonhausen  ...               NaN              355.0   
42664  Altenburger Land  Thonhausen  ...               NaN              240.0   
42665  Altenburger Land  Thonhausen  ...               NaN              349.0   
42666  Altenburger Land  Thonhausen  ...               NaN              296.0   
42667  Altenburger Land  Thonhausen  ...              77.0              307.0   

      id_version_download_datenset_behoerde  \
0                                       NaN   
4                                      59.0   
5                                      59.0   
6                                      59.0   
7                                      59.0   
...                                     ...   
42663                                   NaN   
42664                                   NaN   
42665                                   

In [7]:
genehmigungsdauer=data_not_na[data_not_na["dauer_genehmigung"]>0]
genehmigungsdauer

goal100_id einheit_mastr_nummer               behoerden_einheit_id  \
4           79220      SEE970653437198                SH-03000924205-0002   
6           78441      SEE948056013141                SH-51001900011-0004   
7           79178      SEE969313089747                SH-51001900011-0001   
8           79324      SEE973804784493                SH-51001900011-0005   
9           78680      SEE954883336339                SH-51001900011-0003   
...           ...                  ...                                ...   
42651       24577      SEE947239808451  TH-FAWIND-GOAL100-SEE947239808451   
42653       24645      SEE965077486013  TH-FAWIND-GOAL100-SEE965077486013   
42654       24507      SEE926469864444  TH-FAWIND-GOAL100-SEE926469864444   
42661       24597      SEE953472606747  TH-FAWIND-GOAL100-SEE953472606747   
42667       24769      SEE998013206017  TH-FAWIND-GOAL100-SEE998013206017   

                   name_windpark name_stromerzeugungseinheit  \
4           Windpark Lübeck Nord             WEA2 Pöppendorf   
6      Bürgerwindpark Albersdorf            WEA 4 / V 203772   
7      Bürgerwindpark Albersdorf            WEA 1 / V 203769   
8      Bürgerwindpark Albersdorf            WEA 5 / V 203773   
9      Bürgerwindpark Albersdorf            WEA 3 / V 203771   
...                          ...                         ...   
42651                     Kraasa                    Kraasa 9   
42653                     Kraasa                    Kraasa 8   
42654            Windpark Kraasa                VE-01-206089   
42661                     WEA 05                       WEA 5   
42667   Mark Sahnau / Thonhausen             Thonhausen WEA6   

      einheit_betriebsstatus  ags_gemeinde          bundesland  \
4                 In Betrieb     1003000.0  Schleswig-Holstein   
6                 In Betrieb     1051001.0  Schleswig-Holstein   
7                 In Betrieb     1051001.0  Schleswig-Holstein   
8                 In Betrieb     1051001.0  Schleswig-Holstein   
9                 In Betrieb     1051001.0  Schleswig-Holstein   
...                      ...           ...                 ...   
42651             In Betrieb    16077044.0           Thüringen   
42653             In Betrieb    16077044.0           Thüringen   
42654             In Betrieb    16077044.0           Thüringen   
42661             In Betrieb    16077044.0           Thüringen   
42667             In Betrieb    16077047.0           Thüringen   

              landkreis     gemeinde  ... dauer_genehmigung  \
4                Lübeck       Lübeck  ...             203.0   
6          Dithmarschen   Albersdorf  ...             258.0   
7          Dithmarschen   Albersdorf  ...             258.0   
8          Dithmarschen   Albersdorf  ...             258.0   
9          Dithmarschen   Albersdorf  ...             258.0   
...                 ...          ...  ...               ...   
42651  Altenburger Land  Starkenberg  ...             311.0   
42653  Altenburger Land  Starkenberg  ...             311.0   
42654  Altenburger Land  Starkenberg  ...             279.0   
42661  Altenburger Land  Starkenberg  ...             608.0   
42667  Altenburger Land   Thonhausen  ...              77.0   

      dauer_realisierung id_version_download_datenset_behoerde  \
4                  539.0                                  59.0   
6                  192.0                                  59.0   
7                  193.0                                  59.0   
8                  200.0                                  59.0   
9                  192.0                                  59.0   
...                  ...                                   ...   
42651              412.0                                  23.0   
42653              378.0                                  23.0   
42654               57.0                                  23.0   
42661              300.0                                  23.0   
42667              307.0             

In [23]:
median_dauer_bl=genehmigungsdauer.groupby("bundesland")["dauer_genehmigung"].median()
median_dauer_bl

bundesland
Baden-Württemberg         456.0
Brandenburg               579.0
Hessen                    481.0
Mecklenburg-Vorpommern    594.0
Nordrhein-Westfalen       434.0
Rheinland-Pfalz           427.0
Saarland                  366.0
Sachsen                   537.0
Schleswig-Holstein        301.0
Thüringen                 375.0
Name: dauer_genehmigung, dtype: float64

In [24]:
max_dauer_bl=genehmigungsdauer.groupby("bundesland")["dauer_genehmigung"].quantile(.90)
max_dauer_bl

bundesland
Baden-Württemberg         1400.0
Brandenburg               1401.0
Hessen                    1316.5
Mecklenburg-Vorpommern     594.0
Nordrhein-Westfalen       1060.0
Rheinland-Pfalz           1251.4
Saarland                  1115.0
Sachsen                    866.0
Schleswig-Holstein         914.0
Thüringen                 1056.0
Name: dauer_genehmigung, dtype: float64

In [25]:
min_dauer_bl=genehmigungsdauer.groupby("bundesland")["dauer_genehmigung"].quantile(.10)
min_dauer_bl

bundesland
Baden-Württemberg         184.0
Brandenburg               254.0
Hessen                    220.0
Mecklenburg-Vorpommern    594.0
Nordrhein-Westfalen       204.2
Rheinland-Pfalz           138.0
Saarland                  144.0
Sachsen                   447.0
Schleswig-Holstein        163.0
Thüringen                 167.4
Name: dauer_genehmigung, dtype: float64

In [30]:
min_max_bl=pd.merge(min_dauer_bl,max_dauer_bl,on="bundesland",suffixes=("_min","_max"))
min_max_med_bl=pd.merge(median_dauer_bl,min_max_bl,on="bundesland")
min_max_med_bl=min_max_med_bl.reset_index(drop=False)
min_max_med_bl.to_csv("min_max_median_bl.csv",index=False)

In [8]:
genehmigungsdauer_count=genehmigungsdauer[["ags_landkreis","dauer_genehmigung"]].groupby("ags_landkreis").count().reset_index()
genehmigungsdauer_count

ags_landkreis  dauer_genehmigung
0           01003                  1
1           01051                648
2           01053                 36
3           01054                709
4           01055                173
..            ...                ...
154         16073                 13
155         16074                 25
156         16075                  2
157         16076                 16
158         16077                  5

[159 rows x 2 columns]

In [9]:
kreise_mindest_list=genehmigungsdauer_count[genehmigungsdauer_count["dauer_genehmigung"]>=5]["ags_landkreis"].tolist()
kreise_mindest_list

['01051',
 '01053',
 '01054',
 '01055',
 '01056',
 '01057',
 '01058',
 '01059',
 '01060',
 '01061',
 '01062',
 '05154',
 '05162',
 '05166',
 '05170',
 '05358',
 '05362',
 '05366',
 '05370',
 '05374',
 '05382',
 '05554',
 '05558',
 '05562',
 '05566',
 '05570',
 '05762',
 '05766',
 '05770',
 '05774',
 '05914',
 '05958',
 '05962',
 '05966',
 '05970',
 '05974',
 '06431',
 '06432',
 '06434',
 '06435',
 '06437',
 '06439',
 '06440',
 '06531',
 '06532',
 '06533',
 '06534',
 '06535',
 '06631',
 '06632',
 '06633',
 '06634',
 '06635',
 '06636',
 '07132',
 '07133',
 '07134',
 '07135',
 '07137',
 '07140',
 '07141',
 '07143',
 '07231',
 '07232',
 '07233',
 '07235',
 '07319',
 '07331',
 '07332',
 '07334',
 '07335',
 '07336',
 '07337',
 '07338',
 '07339',
 '07340',
 '08117',
 '08119',
 '08126',
 '08127',
 '08128',
 '08136',
 '08225',
 '08237',
 '08317',
 '08325',
 '08415',
 '08425',
 '08436',
 '08437',
 '10041',
 '10042',
 '10043',
 '10044',
 '10045',
 '10046',
 '12052',
 '12053',
 '12060',
 '12061',


In [10]:
mindest_zahl_genehmigungen=genehmigungsdauer[genehmigungsdauer["ags_landkreis"].isin(kreise_mindest_list)]
median_time_to_genehmigung=mindest_zahl_genehmigungen[["ags_landkreis","landkreis","dauer_genehmigung"]].groupby(["landkreis","ags_landkreis"]).median().reset_index()
median_time_to_genehmigung

landkreis ags_landkreis  dauer_genehmigung
0              Alb-Donau-Kreis         08425              251.0
1             Altenburger Land         16077              311.0
2    Altenkirchen (Westerwald)         07132             1733.0
3                  Alzey-Worms         07331              244.5
4                 Bad Dürkheim         07332              329.0
..                         ...           ...                ...
125                      Wesel         05170              598.0
126            Westerwaldkreis         07143              372.0
127              Wetteraukreis         06440              644.0
128                      Worms         07319              210.0
129                    Zwickau         14524              537.0

[130 rows x 3 columns]

In [11]:
median_time_to_genehmigung=median_time_to_genehmigung.sort_values(by="dauer_genehmigung")
median_time_to_genehmigung.head(50)

landkreis ags_landkreis  dauer_genehmigung
18                 Eichsfeld         16061              102.0
72               Ostalbkreis         08136              184.0
25              Freudenstadt         08237              186.0
111      Südliche Weinstraße         07337              186.0
128                    Worms         07319              210.0
94      Saale-Holzland-Kreis         16074              211.0
61     Neckar-Odenwald-Kreis         08225              216.0
23                Euskirchen         05366              219.0
89          Rhein-Lahn-Kreis         07141              231.0
3                Alzey-Worms         07331              244.5
17                     Düren         05358              248.0
0            Alb-Donau-Kreis         08425              251.0
62               Neunkirchen         10043              254.0
53              Mainz-Bingen         07339              255.0
16              Dithmarschen         01051              257.0
10                    Borken         05554              259.0
100          Schwäbisch Hall         08127              261.0
19   Eifelkreis Bitburg-Prüm         07232              269.0
123            Weimarer Land         16071              269.0
71              Ortenaukreis         08317              273.0
98       Schleswig-Flensburg         01059              273.0
63             Nordfriesland         01054              284.0
92     Rheingau-Taunus-Kreis         06439              290.0
107                Steinburg         01061              299.0
110                 Sömmerda         16068              304.0
5              Bad Kreuznach         07133              309.0
1           Altenburger Land         16077              311.0
15         Darmstadt-Dieburg         06432              311.0
66                 Oberhavel         12065              316.0
29                     Gotha         16067              316.0
56             Merzig-Wadern         10042              328.5
81            Recklinghausen         05562              328.5
4               Bad Dürkheim         07332              329.0
75                 Paderborn         05774              332.0
27               Germersheim         07334              336.0
43                    Kassel         06633              345.0
108                Steinfurt         05566              355.0
96                 Saarlouis         10044              360.0
86          Rhein-Erft-Kreis         05362              361.0
116    Unstrut-Hainich-Kreis         16064              364.0
42            Kaiserslautern         07335              365.5
104                    Soest         05974              370.0
126          Westerwaldkreis         07143              372.0
7                 Bergstraße         06431              377.0
124      Werra-Meißner-Kreis         06636              377.0
49          Limburg-Weilburg         06533              387.0
34                 Heinsberg         05370              394.0
12                  Coesfeld         05558              397.0
44                     Kleve         05154              401.0
119              Vulkaneifel         07233              403.0

In [32]:
median_time_to_genehmigung.head(10).to_csv("shortest_time.csv",index=False)

In [12]:
median_time_to_genehmigung.tail(50)

landkreis ags_landkreis  dauer_genehmigung
33                   Havelland         12063              542.0
60            Märkischer Kreis         05962              543.0
47             Lahn-Dill-Kreis         06532              544.0
79                    Prignitz         12070              555.5
28                      Gießen         06531              556.0
67       Oberspreewald-Lausitz         12066              560.0
32                       Hagen         05914              562.0
91            Rhein-Sieg-Kreis         05382              570.5
65        Oberbergischer Kreis         05374              576.0
11                 Cochem-Zell         07135              592.0
30                       Greiz         16076              594.0
125                      Wesel         05170              598.0
70                        Olpe         05966              599.0
9                   Birkenfeld         07134              614.0
59           Märkisch-Oderland         12064              615.0
52           Main-Tauber-Kreis         08128              620.5
120        Waldeck-Frankenberg         06635              621.0
102        Siegen-Wittgenstein         05970              624.0
114             Trier-Saarburg         07235              627.0
101                   Segeberg         01060              638.0
127              Wetteraukreis         06440              644.0
13                     Cottbus         12052              653.0
83             Rems-Murr-Kreis         08119              667.0
37          Hochsauerlandkreis         05958              680.0
26                       Fulda         06631              681.0
78          Potsdam-Mittelmark         12069              694.0
113             Teltow-Fläming         12072              707.0
85                  Reutlingen         08415              711.0
14             Dahme-Spreewald         12061              730.0
57             Minden-Lübbecke         05770              755.5
31                   Göppingen         08117              762.0
35          Hersfeld-Rotenburg         06632              789.0
69                  Oder-Spree         12067              827.0
87        Rhein-Hunsrück-Kreis         07140              830.0
105                Spree-Neiße         12071              841.0
50                       Lippe         05766              858.0
93                    Rottweil         08325              880.0
76                   Pinneberg         01056              890.0
68               Odenwaldkreis         06437              921.0
55               Mayen-Koblenz         07137              949.0
24            Frankfurt (Oder)         12053              958.0
74          Ostprignitz-Ruppin         12068              972.0
117                    Viersen         05166             1043.0
97             Saarpfalz-Kreis         10045             1115.0
22             Erzgebirgskreis         14521             1177.0
95         Saalfeld-Rudolstadt         16073             1183.0
103                Sigmaringen         08437             1400.0
88           Rhein-Kreis Neuss         05162             1572.5
2    Altenkirchen (Westerwald)         07132             1733.0
21                      Erfurt         16051             2996.0

In [13]:
median_time_to_genehmigung.to_csv("median_time_to_genehmigung.csv",index=False) 

In [21]:
dauer_realisierung=data[data["dauer_realisierung"]>0]
dauer_realisierung

goal100_id einheit_mastr_nummer               behoerden_einheit_id  \
4           79220      SEE970653437198                SH-03000924205-0002   
6           78441      SEE948056013141                SH-51001900011-0004   
7           79178      SEE969313089747                SH-51001900011-0001   
8           79324      SEE973804784493                SH-51001900011-0005   
9           78680      SEE954883336339                SH-51001900011-0003   
...           ...                  ...                                ...   
42663       41655      SEE905015577458                                NaN   
42664       41828      SEE929841659676                                NaN   
42665       29924      SEE924115847834                                NaN   
42666       24143      SEE924538245743                SN-09000000004-0002   
42667       24769      SEE998013206017  TH-FAWIND-GOAL100-SEE998013206017   

                      name_windpark name_stromerzeugungseinheit  \
4              Windpark Lübeck Nord             WEA2 Pöppendorf   
6         Bürgerwindpark Albersdorf            WEA 4 / V 203772   
7         Bürgerwindpark Albersdorf            WEA 1 / V 203769   
8         Bürgerwindpark Albersdorf            WEA 5 / V 203773   
9         Bürgerwindpark Albersdorf            WEA 3 / V 203771   
...                             ...                         ...   
42663  meridian Windpark Thonhausen                       WEA 4   
42664  meridian Windpark Thonhausen                       WEA 7   
42665  meridian Windpark Thonhausen                       WEA 6   
42666      Mark Sahnau / Thonhausen            Mark Sahnau WEA2   
42667      Mark Sahnau / Thonhausen             Thonhausen WEA6   

      einheit_betriebsstatus  ags_gemeinde          bundesland  \
4                 In Betrieb     1003000.0  Schleswig-Holstein   
6                 In Betrieb     1051001.0  Schleswig-Holstein   
7                 In Betrieb     1051001.0  Schleswig-Holstein   
8                 In Betrieb     1051001.0  Schleswig-Holstein   
9                 In Betrieb     1051001.0  Schleswig-Holstein   
...                      ...           ...                 ...   
42663             In Betrieb    16077047.0           Thüringen   
42664             In Betrieb    16077047.0           Thüringen   
42665             In Betrieb    16077047.0           Thüringen   
42666             In Betrieb    16077047.0           Thüringen   
42667             In Betrieb    16077047.0           Thüringen   

              landkreis    gemeinde  ... dauer_genehmigung dauer_realisierung  \
4                Lübeck      Lübeck  ...             203.0              539.0   
6          Dithmarschen  Albersdorf  ...             258.0              192.0   
7          Dithmarschen  Albersdorf  ...             258.0              193.0   
8          Dithmarschen  Albersdorf  ...             258.0              200.0   
9          Dithmarschen  Albersdorf  ...             258.0              192.0   
...                 ...         ...  ...               ...                ...   
42663  Altenburger Land  Thonhausen  ...               NaN              355.0   
42664  Altenburger Land  Thonhausen  ...               NaN              240.0   
42665  Altenburger Land  Thonhausen  ...               NaN              349.0   
42666  Altenburger Land  Thonhausen  ...               NaN              296.0   
42667  Altenburger Land  Thonhausen  ...              77.0              307.0   

      id_version_download_datenset_behoerde  \
4                                      59.0   
6                                      59.0   
7                                      59.0   
8                                      59.0   
9                                      59.0   
...                                     ...   
42663                                   NaN   
42664                                   NaN   
42665                                   NaN   
42666                                  34

In [22]:
realisierungsdauer_count=dauer_realisierung[["ags_landkreis","dauer_realisierung"]].groupby("ags_landkreis").count().reset_index()
realisierungsdauer_count

ags_landkreis  dauer_realisierung
0           01003                   1
1           01051                 830
2           01053                  60
3           01054                 793
4           01055                 261
..            ...                 ...
292         16073                   4
293         16074                  62
294         16075                  22
295         16076                  14
296         16077                  49

[297 rows x 2 columns]

In [23]:
kreise_mindest_real=realisierungsdauer_count[realisierungsdauer_count["dauer_realisierung"]>=5]["ags_landkreis"]
kreise_mindest_real_list=kreise_mindest_real.tolist()

In [24]:
dauer_realisierung_mindest=dauer_realisierung[dauer_realisierung["ags_landkreis"].isin(kreise_mindest_real_list)]
dauer_realisierung_mindest

goal100_id einheit_mastr_nummer               behoerden_einheit_id  \
6           78441      SEE948056013141                SH-51001900011-0004   
7           79178      SEE969313089747                SH-51001900011-0001   
8           79324      SEE973804784493                SH-51001900011-0005   
9           78680      SEE954883336339                SH-51001900011-0003   
10          79070      SEE966072006992                SH-51001900011-0002   
...           ...                  ...                                ...   
42663       41655      SEE905015577458                                NaN   
42664       41828      SEE929841659676                                NaN   
42665       29924      SEE924115847834                                NaN   
42666       24143      SEE924538245743                SN-09000000004-0002   
42667       24769      SEE998013206017  TH-FAWIND-GOAL100-SEE998013206017   

                      name_windpark name_stromerzeugungseinheit  \
6         Bürgerwindpark Albersdorf            WEA 4 / V 203772   
7         Bürgerwindpark Albersdorf            WEA 1 / V 203769   
8         Bürgerwindpark Albersdorf            WEA 5 / V 203773   
9         Bürgerwindpark Albersdorf            WEA 3 / V 203771   
10        Bürgerwindpark Albersdorf            WEA 2 / V 203770   
...                             ...                         ...   
42663  meridian Windpark Thonhausen                       WEA 4   
42664  meridian Windpark Thonhausen                       WEA 7   
42665  meridian Windpark Thonhausen                       WEA 6   
42666      Mark Sahnau / Thonhausen            Mark Sahnau WEA2   
42667      Mark Sahnau / Thonhausen             Thonhausen WEA6   

      einheit_betriebsstatus  ags_gemeinde          bundesland  \
6                 In Betrieb     1051001.0  Schleswig-Holstein   
7                 In Betrieb     1051001.0  Schleswig-Holstein   
8                 In Betrieb     1051001.0  Schleswig-Holstein   
9                 In Betrieb     1051001.0  Schleswig-Holstein   
10                In Betrieb     1051001.0  Schleswig-Holstein   
...                      ...           ...                 ...   
42663             In Betrieb    16077047.0           Thüringen   
42664             In Betrieb    16077047.0           Thüringen   
42665             In Betrieb    16077047.0           Thüringen   
42666             In Betrieb    16077047.0           Thüringen   
42667             In Betrieb    16077047.0           Thüringen   

              landkreis    gemeinde  ... dauer_genehmigung dauer_realisierung  \
6          Dithmarschen  Albersdorf  ...             258.0              192.0   
7          Dithmarschen  Albersdorf  ...             258.0              193.0   
8          Dithmarschen  Albersdorf  ...             258.0              200.0   
9          Dithmarschen  Albersdorf  ...             258.0              192.0   
10         Dithmarschen  Albersdorf  ...             258.0              199.0   
...                 ...         ...  ...               ...                ...   
42663  Altenburger Land  Thonhausen  ...               NaN              355.0   
42664  Altenburger Land  Thonhausen  ...               NaN              240.0   
42665  Altenburger Land  Thonhausen  ...               NaN              349.0   
42666  Altenburger Land  Thonhausen  ...               NaN              296.0   
42667  Altenburger Land  Thonhausen  ...              77.0              307.0   

      id_version_download_datenset_behoerde  \
6                                      59.0   
7                                      59.0   
8                                      59.0   
9                                      59.0   
10                                     59.0   
...                                     ...   
42663                                   NaN   
42664                                   NaN   
42665                                   NaN   
42666                                  34

In [26]:
dauer_realisierung_mindest[dauer_realisierung_mindest.landkreis.str.contains("Erfurt")].sort_values(by="dauer_realisierung")

goal100_id einheit_mastr_nummer               behoerden_einheit_id  \
41607       24600      SEE954018466771  TH-FAWIND-GOAL100-SEE954018466771   
41608       38145      SEE959393004785                                NaN   
41575       24529      SEE932471928456  TH-FAWIND-GOAL100-SEE932471928456   
41578       34940      SEE902132723218                                NaN   
41580       34945      SEE915327261174                                NaN   
41579       34943      SEE922411163153                                NaN   
41587       34950      SEE991418465737                                NaN   
41583       34949      SEE994547937892                                NaN   
41596       34952      SEE913659595509                                NaN   
41593       34954      SEE934461145102                                NaN   
41595       34953      SEE990494922448                                NaN   
41594       34951      SEE902941736171                                NaN   
41582       34948      SEE973527707113                                NaN   
41581       34946      SEE970686952231                                NaN   
41584       24523      SEE930372015268  TH-FAWIND-GOAL100-SEE930372015268   
41586       24610      SEE956823799938  TH-FAWIND-GOAL100-SEE956823799938   
41585       24643      SEE964410737935  TH-FAWIND-GOAL100-SEE964410737935   
41589       24498      SEE924182704337  TH-FAWIND-GOAL100-SEE924182704337   
41590       24463      SEE917172170892  TH-FAWIND-GOAL100-SEE917172170892   
41591       24441      SEE909386131769  TH-FAWIND-GOAL100-SEE909386131769   
41592       24698      SEE977382434764  TH-FAWIND-GOAL100-SEE977382434764   
41577       24606      SEE955990368176  TH-FAWIND-GOAL100-SEE955990368176   

                          name_windpark   name_stromerzeugungseinheit  \
41607                      Kerspleben 2                        531507   
41608                      Kerspleben 1                         53474   
41575            CEE Windpark Töttleben  CEE Windpark Töttleben WEA 1   
41578  Windpark Möbisburg GmbH ＆ Co. KG             WEA 1 - Nr. 78418   
41580  Windpark Möbisburg GmbH ＆ Co. KG             WEA 3 - Nr. 78420   
41579  Windpark Möbisburg GmbH ＆ Co. KG             WEA 2 - Nr. 78419   
41587  Windpark Möbisburg GmbH ＆ Co. KG             WEA 7 - Nr. 78424   
41583  Windpark Möbisburg GmbH ＆ Co. KG             WEA 6 - Nr. 78423   
41596  Windpark Möbisburg GmbH ＆ Co. KG             WEA 9 - Nr. 78426   
41593  Windpark Möbisburg GmbH ＆ Co. KG            WEA 11 - Nr. 78428   
41595  Windpark Möbisburg GmbH ＆ Co. KG            WEA 10 - Nr. 78427   
41594  Windpark Möbisburg GmbH ＆ Co. KG             WEA 8 - Nr. 78425   
41582  Windpark Möbisburg GmbH ＆ Co. KG             WEA 5 - Nr. 78422   
41581  Windpark Möbisburg GmbH ＆ Co. KG             WEA 4 - Nr. 78421   
41584                     WP Frienstedt           24 WEA Frienstedt I   
41586                     WP Frienstedt         24 WEA Frienstedt III   
41585                     WP Frienstedt          24 WEA Frienstedt II   
41589                     WP Frienstedt          24 WEA Frienstedt IV   
41590                     WP Frienstedt           24 WEA Frienstedt V   
41591                     WP Frienstedt          24 WEA Frienstedt VI   
41592                     WP Frienstedt         24 WEA Frienstedt VII   
41577                     WP Frienstedt        24 WEA Frienstedt VIII   

      einheit_betriebsstatus  ags_gemeinde bundesland landkreis gemeinde  ...  \
41607             In Betrieb    16051000.0  Thüringen    Erfurt   Erfurt  ...   
41608             In Betrieb    16051000.0  Thüringen    Erfurt   Erfurt  ...   
41575             In Betrieb    16051000.0  Thüringen    Erfurt   Erfurt  ...   
41578             In Betrieb    16051000.0  Thüringen    Erfurt   Erfurt  ...   
41580             In Betrieb    16051000.0  Thüringen    Erfurt   Erfurt  ...   
41579             In Betrieb    16051000.0  Thüringen    Erfurt   Erf

In [90]:
median_time_to_realisierung=dauer_realisierung_mindest[["ags_landkreis","landkreis","dauer_realisierung"]].groupby(["landkreis","ags_landkreis"]).median().reset_index()

median_time_to_genehmigung

landkreis ags_landkreis  dauer_genehmigung
0              Alb-Donau-Kreis         08425              251.0
1             Altenburger Land         16077              311.0
2    Altenkirchen (Westerwald)         07132             1733.0
3                  Alzey-Worms         07331              244.5
4                 Bad Dürkheim         07332              329.0
..                         ...           ...                ...
125                      Wesel         05170              598.0
126            Westerwaldkreis         07143              372.0
127              Wetteraukreis         06440              644.0
128                      Worms         07319              210.0
129                    Zwickau         14524              537.0

[130 rows x 3 columns]

In [91]:
median_time_to_realisierung.sort_values(by="dauer_realisierung").head(50)

landkreis ags_landkreis  dauer_realisierung
107                            Krefeld         05114                62.0
183                   Rhein-Lahn-Kreis         07141                64.0
251                              Worms         07319                69.5
7                            Ammerland         03451                76.0
46                            Dortmund         05913               132.0
61                Freiburg im Breisgau         08311               159.0
216   Sächsische Schweiz-Osterzgebirge         14628               163.0
72                 Grafschaft Bentheim         03456               211.0
121                           Lüneburg         03355               211.0
3                     Altenburger Land         16077               216.0
156                          Oberhavel         12065               216.5
5                          Alzey-Worms         07331               217.0
110                    Kyffhäuserkreis         16065               219.0
229                             Vechta         03460               220.0
143                  Neumarkt i.d.OPf.         09373               223.0
60                    Frankfurt (Oder)         12053               227.0
84                           Havelland         12063               231.0
18                             Bautzen         14625               232.0
155               Oberbergischer Kreis         05374               237.0
0                            Ahrweiler         07131               240.0
191               Saale-Holzland-Kreis         16074               244.0
66                                Gera         16052               250.0
27                              Bremen         04011               251.0
247                      Wilhelmshaven         03405               253.5
88                           Heilbronn         08125               253.5
4               Altmarkkreis Salzwedel         15081               255.0
105                          Kitzingen         09675               258.0
139                    Mönchengladbach         05116               259.0
96                     Hochtaunuskreis         06434               262.0
146   Neustadt a.d.Aisch-Bad Windsheim         09575               264.0
134                         Miltenberg         09676               265.5
145  Neustadt a.d. Aisch-Bad Windsheim         09575               265.5
236                        Vulkaneifel         07233               266.0
148                      Nordfriesland         01054               266.0
249                           Wittmund         03462               267.0
248                         Wittenberg         15091               267.0
113                               Leer         03457               270.5
234              Vorpommern-Greifswald         13075               271.0
115                            Leipzig         14729               271.0
45                    Donnersbergkreis         07333               271.0
185              Rheingau-Taunus-Kreis         06439               271.5
202                        Schweinfurt         09678               278.0
217                           Sömmerda         16068               280.0
63                           Friesland         03455               280.0
93                 Herzogtum Lauenburg         01053               282.0
12                              Aurich         03452               282.0
144                        Neunkirchen         10043               283.0
42                            Diepholz         03251               284.5
195                    Saarpfalz-Kreis         10045               286.0
10                             Ansbach         09571               287.0

In [92]:
median_time_to_realisierung.sort_values(by="dauer_realisierung").tail(50)

landkreis ags_landkreis  dauer_realisierung
171        Pfaffenhofen a.d. Ilm         09186               483.0
83                          Harz         15085               485.0
213                      Stendal         15090               486.5
36                      Coesfeld         05558               489.0
178              Region Hannover         03241               489.5
117                        Lippe         05766               490.0
219                 Südwestpfalz         07340               493.0
238                    Warendorf         05570               494.5
153              Nürnberger Land         09574               497.0
52                         Emden         03402               503.0
116             Limburg-Weilburg         06533               509.0
231                      Viersen         05166               517.0
233                Vogtlandkreis         14523               521.0
64                         Fulda         06631               555.0
225                       Uelzen         03360               557.0
240                Weimarer Land         16071               563.0
91                       Herford         05758               568.5
29               Burgenlandkreis         15084               571.0
34                        Coburg         09473               573.0
149                   Nordhausen         16062               574.5
85                      Haßberge         09674               586.0
1              Aichach-Friedberg         09771               587.5
184            Rhein-Pfalz-Kreis         07338               590.0
43          Dillingen a.d. Donau         09773               592.0
200           Schwalm-Eder-Kreis         06634               607.0
11                      Augsburg         09772               608.0
194                    Saarlouis         10044               624.0
92            Hersfeld-Rotenburg         06632               636.5
87                    Heidenheim         08135               648.0
253   Wunsiedel i.Fichtelgebirge         09479               651.0
208                  Spree-Neiße         12071               658.0
221                Tirschenreuth         09377               661.0
201                   Schwandorf         09376               664.0
252  Wunsiedel i. Fichtelgebirge         09479               668.0
9                        Ansbach         09561               673.0
97                           Hof         09475               673.0
70                        Goslar         03153               680.0
108                     Kulmbach         09477               681.0
41                 Dessau-Roßlau         15001               702.0
37                       Cottbus         12052               782.0
120            Lüchow-Dannenberg         03354               798.5
78                         Hagen         05914               826.0
16                       Bamberg         09471               856.0
206                  Sigmaringen         08437               889.5
177                   Regensburg         09375               894.0
186                Rhön-Grabfeld         09673               902.5
56                        Erfurt         16051               920.0
138             Märkischer Kreis         05962               950.0
122                    Magdeburg         15003              1086.0
101                    Ilm-Kreis         16070              1378.0

In [100]:
genehmigung_realisierung_merged=pd.merge(median_time_to_genehmigung,median_time_to_realisierung,on=["ags_landkreis","landkreis"])
genehmigung_realisierung_merged

landkreis ags_landkreis  dauer_genehmigung  dauer_realisierung
0     Alb-Donau-Kreis         08425              251.0               442.0
1    Altenburger Land         16077              311.0               216.0
2         Alzey-Worms         07331              244.5               217.0
3        Bad Dürkheim         07332              329.0               333.0
4       Bad Kreuznach         07133              309.0               472.0
..                ...           ...                ...                 ...
117             Wesel         05170              598.0               317.0
118   Westerwaldkreis         07143              372.0               350.0
119     Wetteraukreis         06440              644.0               387.0
120             Worms         07319              210.0                69.5
121           Zwickau         14524              537.0               472.0

[122 rows x 4 columns]

In [108]:
genehmigung_realisierung_merged_rank_1=genehmigung_realisierung_merged.sort_values(by="dauer_genehmigung").reset_index(drop=True).reset_index()
genehmigung_realisierung_merged_rank_1=genehmigung_realisierung_merged_rank_1.rename(columns={"index":"rank_genehmigung"})

In [109]:
genehmigung_realisierung_merged_rank_2=genehmigung_realisierung_merged_rank_1.sort_values(by="dauer_realisierung").reset_index(drop=True).reset_index()
genehmigung_realisierung_merged_rank_2=genehmigung_realisierung_merged_rank_2.rename(columns={"index":"rank_realisierung"})
genehmigung_realisierung_merged_rank_2

rank_realisierung  rank_genehmigung         landkreis ags_landkreis  \
0                    0                 8  Rhein-Lahn-Kreis         07141   
1                    1                 4             Worms         07319   
2                    2                27  Altenburger Land         16077   
3                    3                29         Oberhavel         12065   
4                    4                 9       Alzey-Worms         07331   
..                 ...               ...               ...           ...   
117                117                84             Hagen         05914   
118                118               119       Sigmaringen         08437   
119                119               121            Erfurt         16051   
120                120                79  Märkischer Kreis         05962   
121                121                51         Ilm-Kreis         16070   

     dauer_genehmigung  dauer_realisierung  
0                231.0                64.0  
1                210.0                69.5  
2                311.0               216.0  
3                316.0               216.5  
4                244.5               217.0  
..                 ...                 ...  
117              562.0               826.0  
118             1400.0               889.5  
119             2996.0               920.0  
120              543.0               950.0  
121              409.0              1378.0  

[122 rows x 6 columns]

In [110]:
genehmigung_realisierung_merged_rank_2["mean_rank"]=genehmigung_realisierung_merged_rank_2[["rank_genehmigung","rank_realisierung"]].mean(axis=1)
genehmigung_realisierung_merged_rank_2

rank_realisierung  rank_genehmigung         landkreis ags_landkreis  \
0                    0                 8  Rhein-Lahn-Kreis         07141   
1                    1                 4             Worms         07319   
2                    2                27  Altenburger Land         16077   
3                    3                29         Oberhavel         12065   
4                    4                 9       Alzey-Worms         07331   
..                 ...               ...               ...           ...   
117                117                84             Hagen         05914   
118                118               119       Sigmaringen         08437   
119                119               121            Erfurt         16051   
120                120                79  Märkischer Kreis         05962   
121                121                51         Ilm-Kreis         16070   

     dauer_genehmigung  dauer_realisierung  mean_rank  
0                231.0                64.0        4.0  
1                210.0                69.5        2.5  
2                311.0               216.0       14.5  
3                316.0               216.5       16.0  
4                244.5               217.0        6.5  
..                 ...                 ...        ...  
117              562.0               826.0      100.5  
118             1400.0               889.5      118.5  
119             2996.0               920.0      120.0  
120              543.0               950.0       99.5  
121              409.0              1378.0       86.0  

[122 rows x 7 columns]

In [112]:
genehmigung_realisierung_merged_rank_2.sort_values(by="mean_rank").head(20)

rank_realisierung  rank_genehmigung              landkreis ags_landkreis  \
1                   1                 4                  Worms         07319   
0                   0                 8       Rhein-Lahn-Kreis         07141   
4                   4                 9            Alzey-Worms         07331   
9                   9                 5   Saale-Holzland-Kreis         16074   
20                 20                 1            Ostalbkreis         08136   
17                 17                12            Neunkirchen         10043   
22                 22                 7             Euskirchen         05366   
2                   2                27       Altenburger Land         16077   
3                   3                29              Oberhavel         12065   
12                 12                21          Nordfriesland         01054   
14                 14                22  Rheingau-Taunus-Kreis         06439   
35                 35                 2    Südliche Weinstraße         07337   
15                 15                24               Sömmerda         16068   
34                 34                 6  Neckar-Odenwald-Kreis         08225   
5                   5                50        Kyffhäuserkreis         16065   
46                 46                13           Mainz-Bingen         07339   
19                 19                40         Kaiserslautern         07335   
11                 11                49            Vulkaneifel         07233   
26                 26                34            Germersheim         07334   
47                 47                16        Schwäbisch Hall         08127   

    dauer_genehmigung  dauer_realisierung  mean_rank  
1               210.0                69.5        2.5  
0               231.0                64.0        4.0  
4               244.5               217.0        6.5  
9               211.0               244.0        7.0  
20              184.0               297.0       10.5  
17              254.0               283.0       14.5  
22              219.0               307.0       14.5  
2               311.0               216.0       14.5  
3               316.0               216.5       16.0  
12              284.0               266.0       16.5  
14              290.0               271.5       18.0  
35              186.0               325.0       18.5  
15              304.0               280.0       19.5  
34              216.0               325.0       20.0  
5               406.0               219.0       27.5  
46              255.0               347.5       29.5  
19              365.5               290.0       29.5  
11              403.0               266.0       30.0  
26              336.0               312.0       30.0  
47              261.0               349.0       31.5

In [113]:
genehmigung_realisierung_merged_rank_2.sort_values(by="mean_rank").tail(20)

rank_realisierung  rank_genehmigung           landkreis ags_landkreis  \
92                  92                87               Greiz         16076   
79                  79               101  Potsdam-Mittelmark         12069   
78                  78               102      Teltow-Fläming         12072   
64                  64               118     Erzgebirgskreis         14521   
63                  63               120   Rhein-Kreis Neuss         05162   
88                  88                95      Trier-Saarburg         07235   
96                  96                89                Olpe         05966   
94                  94                96            Segeberg         01060   
120                120                79    Märkischer Kreis         05962   
117                117                84               Hagen         05914   
89                  89               113       Mayen-Koblenz         07137   
108                108               100               Fulda         06631   
103                103               110               Lippe         05766   
116                116                98             Cottbus         12052   
99                  99               115  Ostprignitz-Ruppin         12068   
114                114               106  Hersfeld-Rotenburg         06632   
107                107               116             Viersen         05166   
115                115               109         Spree-Neiße         12071   
118                118               119         Sigmaringen         08437   
119                119               121              Erfurt         16051   

     dauer_genehmigung  dauer_realisierung  mean_rank  
92               594.0               453.0       89.5  
79               694.0               419.0       90.0  
78               707.0               416.0       90.0  
64              1177.0               379.0       91.0  
63              1572.5               377.5       91.5  
88               627.0               444.0       91.5  
96               599.0               467.0       92.5  
94               638.0               464.0       95.0  
120              543.0               950.0       99.5  
117              562.0               826.0      100.5  
89               949.0               446.0      101.0  
108              681.0               555.0      104.0  
103              858.0               490.0      106.5  
116              653.0               782.0      107.0  
99               972.0               473.0      107.0  
114              789.0               636.5      110.0  
107             1043.0               517.0      111.5  
115              841.0               658.0      112.0  
118             1400.0               889.5      118.5  
119             2996.0               920.0      120.0

In [114]:
genehmigung_realisierung_merged_rank_2.to_csv("genehmigungen_realisierung.csv",index=False)

In [ ]:
# Viersen called NEW Mönchengladbach
# Erfurt called VSB
#